In [2]:
import scipy.stats as stats
import numpy as np
from numpy.linalg import inv
import matplotlib.pyplot as plt
import random
import sys
import corner
import pystan
from statsmodels.graphics.tsaplots import plot_acf
import seaborn as sns
import pandas as pd

np.random.seed(1234)

In [14]:
# The aim of this practical is to construct and constrain a Bayesian hierarchical model for the 
# distribution of masses of black holes, based on LIGO O1 and O2 observations. To describe the 
# gravitational wave measurements we will use the posterior distribution on the chirp mass and
# symmetric mass ratio. The median and 90% symmetric credible intervals for the events in the 
# GWTC-1 paper were as follows. Entries are written in the form 
#      GWXXX: [Mc_low, Mc_med, Mc_high]   [eta_low, eta_med, eta_high]
# where Mc_low, Mc_med and Mc_high are, respectively, the lower edge of the 90% credible interval, 
# the median and the upper edge of the 90% credible interval for the chirp mass, and eta_low, 
# eta_med, eta_high are the corresponding quantities for the symmetric mass ratio.

# GW150914: [27.1, 28.6, 30.3] [0.2397, 0.2487, 0.2500] 
# GW151012: [14.0, 15.2, 17.3] [0.1547, 0.2334, 0.2498] 
# GW151226: [8.6, 8.9, 9.2] [0.1514, 0.2301, 0.2498] 
# GW170104: [19.6, 21.4, 23.6] [0.2082, 0.2386, 0.2498] 
# GW170608: [7.7, 7.9, 8.1] [0.1870, 0.2417, 0.2499] 
# GW170729: [30.6, 35.4, 41.9] [0.2030, 0.2408, 0.2499]
# GW170809: [23.2, 24.9, 27.0] [0.2122, 0.2409, 0.2499] 
# GW170814: [23.0, 24.1, 25.5] [0.2339, 0.2478, 0.2500] 
# GW170818: [24.8, 26.5, 28.6] [0.2241, 0.2453, 0.2499] 
# GW170823: [25.6, 29.2, 33.8] [0.2130, 0.2446, 0.2499] 

# To aid computation we will approximate these posterior distributions. The chirp mass posteriors 
# will be approximated by a Gaussian, with mean equal to Mc_med and standard deviation equal to 
# (Mc_high-Mc_low)/3.29. For the symmetric mass ratio posteriors, we will use a B(a,1) distribution
# approximation for 4*eta. As can be seen from the Table above, the eta posteriors are not Gaussian, 
# but peak at the upper end of the allowed range, near eta = 0.25. A Beta(a,1) distribution has a 
# similar form, on the interval [0,1], which is why we represent the distribution in this way. For
# B(a,1), the median value satisfies x^a = 0.5 and the lower 5% point satisfies x^a = 0.05. Hence 
# we can choose a based on the median value or the lower end of the 90% credible interval, for the 
# median the formula is a = ln(1/2)/(ln(4*eta_med)). We'll try both below.

Mc_low=np.array([27.1,14.0,8.6,19.6,7.7,30.6,23.2,23.0,24.8,25.6])
Mc_med=np.array([28.6,15.2,8.9,21.4,7.9,35.4,24.9,24.1,26.5,29.2])
Mc_high=np.array([30.3,17.3,9.2,23.6,8.1,41.9,27.0,25.5,28.6,33.8])
eta_low=np.array([0.2397,0.1547,0.1514,0.2082,0.187,0.203,0.2122,0.2339,0.2241,0.213])
eta_med=np.array([0.2487,0.2334,0.2301,0.2386,0.2417,0.2408,0.2409,0.2478,0.2453,0.2446])
eta_high=np.array([0.25,0.2499,0.2498,0.2498,0.2499,0.2499,0.2499,0.25,0.2499,0.2499])

mc_mean=Mc_med
mc_std=(Mc_high-Mc_low)/3.29
eta_a=np.log(0.5)/(np.log(4.0*eta_med))
eta_a_alt=np.log(0.05)/(np.log(4.0*eta_low))

In [16]:
# Check the median value corresponding to the a value determined from the lower limit of the eta credible 
# interval and vice versa. The match to the true posterior values is not great, suggesitng the Beta distribution 
# is not a fantastic fit, but we will proceed anyway since we want an analytic form for the distribution.

eta_low_mod=0.25*(0.05**(1.0/eta_a))
eta_med_mod_alt=0.25*(0.5**(1.0/eta_a_alt))
print(eta_low_mod)
print(eta_med_mod)

[0.24442983 0.18577074 0.17468254 0.204332   0.21605585 0.21260025
 0.2129821  0.24062979 0.23031206 0.227485  ]
[0.24757813 0.22372231 0.22260892 0.23963754 0.23375644 0.23823921
 0.24069503 0.24617895 0.243753   0.24090469]


In [ ]:
# The likelihood of the observed data will be modelled for each event as a product of a beta distribution for
# eta and a Gaussian for the chirp mass. We want to constrain the population by using a hierarchical model. 
# First we take a simple truncated power law (model A/B in the GWTC-1 companion paper).
#
#          p(m1, m2 | mmin, mmax, alpha, beta) = C(m1) m1^(-alpha) (m2/m1)^beta for mmin <= m2 <= m1 <= mmax
#
# The function C(m1) is chosen to ensure that the marginal prior on m1 is a power law m1^(-alpha). We first take
# the simplest model, model A, in which we fix mmin=5 and beta = 0, for which C(m1) = (m1-mmin).

# The final quantity we need is the selection function. As discussed in lectures, gravitational wave detectors 
# are not infinitely sensitive, and only events that are sufficiently loud are detected and used to constrain 
# the population. To incorporate selection effects we must renormalise the likelihood by dividing by the 
# integral over the population model of the probability of detection. We approximate the latter as proportional 
# to m1^2.2 (see Fishbach & Holz for justification of this approximation). The selection function is therefore
#
#           p(D|mmin,mmax,alpha,beta) \propto int_mmin^mmax m1^(2.2-alpha)
#                                     \propto mmax^(3.2-alpha)-mmin^(3.2-alpha)
#

# Exercises

In [ ]:
# 1) Write a pystan model that represents the hierarchical model described above.
#
# 2) Obtain the posterior distribution for model A using pystan. Compute also the posterior predictive 
#    distribution for m1 based on these results.
#
# 3) Adapt your model to fit model B from the GWTC-1 companion paper, in which all four parameters of the power
#    law are allowed to vary.
# 
# 4) How would you need to change the model to fit model C from the GWTC-1 companion paper, which includes both
#    a power law and a Gaussian component?